In [0]:
from pyspark.sql.functions import col, sum, when, mean, countDistinct
from pyspark.sql import functions as F
from pyspark.ml.feature import PCA
from pyspark.ml.feature import VectorAssembler
from pyspark.sql.window import Window
import pyspark.pandas as ps

In [0]:
# Point file path
path = '/databricks-datasets/Rdatasets/data-001/csv/ggplot2/diamonds.csv'

# Load Data
df = spark.read.csv(path, header=True, inferSchema= True)
df = df.filter( col('y') < 30)

# Get only our selected columns
cols = [ 'carat', 'table', 'depth']

df_num = df.select(F.log1p('carat').alias('carat'), 
                   F.log1p('table').alias('table'), 
                   F.log1p('depth').alias('depth'))

# df_num = df.select(F.log1p('x').alias('x'), 
#                    F.log1p('y').alias('y'), 
#                    F.log1p('z').alias('z'), 
#                    F.log1p('table').alias('table'), 
#                    F.log1p('depth').alias('depth'))

In [0]:
df_num.limit(3).display()

carat table depth 0.20701416938432615 4.02535169073515 4.135166556742356 0.1906203596086497 4.127134385045092 4.107589788972121 0.20701416938432615 4.189654742026425 4.05871738457895

### Vectorize the Dataset
The first step to be done when working with MLlib is to vectorize the dataset, as that is the format how MLlib algorithms require the data.

In [0]:
# Transform all features into a vector using VectorAssembler
# We removed price, as this would be our target variable
assembler = VectorAssembler(inputCols= cols, outputCol="features")
prepared_df = assembler.transform(df_num)

In [0]:
display(prepared_df.select('features').limit(2))

features Map(vectorType -> dense, length -> 3, values -> List(0.20701416938432615, 4.02535169073515, 4.135166556742356)) Map(vectorType -> dense, length -> 3, values -> List(0.1906203596086497, 4.127134385045092, 4.107589788972121))

### Running PCA
Now that we have the vectorized version of our data, let's run PCA

In [0]:
from scipy import stats as scs
scs.bartlett( df_num.toPandas()['carat'], 
             df_num.toPandas()['depth'],
             df_num.toPandas()['table'],
            #  df_num.toPandas()['x'], 
            #  df_num.toPandas()['y'],
            #  df_num.toPandas()['z'] 
            )

BartlettResult(statistic=284679.93937348214, pvalue=0.0)

In [0]:
# First, we will run it with all the possible components
pca = PCA(k= len(df_num.columns), inputCol="features")
pca.setOutputCol("pca_features")

# Fit
model = pca.fit(prepared_df)

In [0]:
# See explained variance of the PCs
df_var = ps.DataFrame(model.explainedVariance, columns=['explained_var'])
df_var.insert(0, 'Component', value= ['PC'+str(n) for n in range(1,len(df_num.columns)+1)])
display(df_var)

Component explained_var PC1 0.969359536218893 PC2 0.023390828236009808 PC3 0.007249635545097206

Databricks visualization. Run in Databricks to view.

In [0]:
# Get transformed Output
model.setOutputCol("output")
pca_transformed = model.transform(prepared_df).select('output')

In [0]:
display(pca_transformed)

output Map(vectorType -> dense, length -> 3, values -> List(-0.337854542043682, -2.7279272511201453, 5.078403368525109)) Map(vectorType -> dense, length -> 3, values -> List(-0.32446613567339955, -2.833791365368773, 5.079981934273924)) Map(vectorType -> dense, length -> 3, values -> List(-0.3426183667407044, -2.906836771193466, 5.049966452562161)) Map(vectorType -> dense, length -> 3, values -> List(-0.3870652924383873, -2.772813774386362, 5.1059660041188275)) Map(vectorType -> dense, length -> 3, values -> List(-0.4024765682415171, -2.768508812545547, 5.1193580291946725)) Map(vectorType -> dense, length -> 3, values -> List(-0.3470528920960793, -2.7557749568923597, 5.107740557594817)) Map(vectorType -> dense, length -> 3, values -> List(-0.3470342664094098, -2.757934928841296, 5.100175016362643)) Map(vectorType -> dense, length -> 3, values -> List(-0.3619562129785228, -2.725494136953833, 5.084283911928863)) Map(vectorType -> dense, length -> 3, values -> List(-0.3328907410349031, -2.810613510014358, 5.160262668967488)) Map(vectorType -> dense, length -> 3, values -> List(-0.3408368476058274, -2.835139680786452, 5.073462128678454)) Map(vectorType -> dense, length -> 3, values -> List(-0.3932722573799504, -2.7155941073847125, 5.115533784069199)) Map(vectorType -> dense, length -> 3, values -> List(-0.3384359569574918, -2.739287742723086, 5.103054650440278)) Map(vectorType -> dense, length -> 3, values -> List(-0.33271613063654204, -2.830862619169142, 5.089337919087877)) Map(vectorType -> dense, length -> 3, values -> List(-0.40032287811260375, -2.7057682695361174, 5.083505968806014)) Map(vectorType -> dense, length -> 3, values -> List(-0.31666817904639416, -2.8476048469770308, 5.090764334358518)) Map(vectorType -> dense, length -> 3, values -> List(-0.40998765033530843, -2.778736689563842, 5.0827000971233804)) Map(vectorType -> dense, length -> 3, values -> List(-0.39265599457253014, -2.7068551970237924, 5.080538931849452)) Map(vectorType -> dense, length -> 3, values -> List(-0.3927080255145413, -2.7008213053764476, 5.101673306335624)) Map(vectorType -> dense, length -> 3, values -> List(-0.3937976420294643, -2.7334522815331903, 5.1174262124557215)) Map(vectorType -> dense, length -> 3, values -> List(-0.3953008151661696, -2.787453704212924, 5.11503478911221)) Map(vectorType -> dense, length -> 3, values -> List(-0.3937793048923594, -2.7355787911472125, 5.109977876761629)) Map(vectorType -> dense, length -> 3, values -> List(-0.33794009446277495, -2.7180059618445402, 5.113153784208919)) Map(vectorType -> dense, length -> 3, values -> List(-0.3388916227478372, -2.7638607748689936, 5.080306745228537)) Map(vectorType -> dense, length -> 3, values -> List(-0.40430263576851977, -2.8487359787236746, 5.077187642479022)) Map(vectorType -> dense, length -> 3, values -> List(-0.40425112735439145, -2.85470927418525, 5.056265512851946)) Map(vectorType -> dense, length -> 3, values -> List(-0.33938306943423696, -2.7829609853773043, 5.075645526378264)) Map(vectorType -> dense, length -> 3, values -> List(-0.34704173427857965, -2.7570688996735435, 5.1032083795413286)) Map(vectorType -> dense, length -> 3, values -> List(-0.39426187158034803, -2.75703219686851, 5.098156808982193)) Map(vectorType -> dense, length -> 3, values -> List(-0.34087957302838473, -2.830184925782349, 5.090816707425328)) Map(vectorType -> dense, length -> 3, values -> List(-0.33888780141922104, -2.764303924309068, 5.078754565181686)) Map(vectorType -> dense, length -> 3, values -> List(-0.33885312901248554, -2.768324792225503, 5.064671029501564)) Map(vectorType -> dense, length -> 3, values -> List(-0.3388453545800017, -2.7692263727353645, 5.061513143805483)) Map(vectorType -> dense, length -> 3, values -> List(-0.3399004287507712, -2.797777258522256, 5.084943183340808)) Map(vectorType -> dense, length -> 3, values -> List(-0.3393481125840095, -2.7870148394581986, 5.061446452999871)) Map(vectorType -> dense, length -> 3, values -> List(-0.33944020766806215, -2.7763348

In [0]:
temp = spark.createDataFrame(pca_transformed.collect())
temp = temp.select(col('output').cast('string'))

# split columns
df_transformed = (
    temp
    .select(
        F.split('output', ',')[0][2:15].alias('PC1').cast('float'),
        F.split('output', ',')[1].cast('float').alias('PC2'),
                            #F.split('output', ',')[2].cast('float').alias('PC3'),
                            #F.split('output', ',')[3].cast('float').alias('PC4'),
                            #F.split('output', ',')[4].cast('float').alias('PC5'),
        F.split('output', ',')[2][0:14].alias('PC3').cast('float')       ) 
        .fillna(0)
        )

In [0]:
display(temp.limit(2))

output [-0.337854542043682,-2.7279272511201453,5.078403368525109] [-0.32446613567339955,-2.833791365368773,5.079981934273924]

In [0]:
display(df_transformed.limit(3))

PC1 PC2 PC3 -0.33785453 -2.7279272 5.0784035 -0.32446614 -2.8337913 5.079982 -0.34261838 -2.9068367 5.0499663

In [0]:
# Explained variance array
expl_var = model.explainedVariance

df_transformed = (
        df_transformed
        .withColumn('_c0', F.row_number().over(Window.partitionBy().orderBy(F.lit(1))))
        .withColumn('score', (col('PC1') * expl_var[0]) + (col('PC2') * expl_var[1]) + (col('PC3') * expl_var[2]) ) #+ (col('PC4') * expl_var[3]) + (col('PC5') * expl_var[4]))
        .withColumn('rank', F.dense_rank().over(Window.partitionBy().orderBy('score')) )
        .sort('_c0')
        )

df_transformed.count()

53938

In [0]:
display(df
        .join(df_transformed.select('_c0', 'rank'),
              on='_c0',
              how='inner')
        .sort(col('rank'))
        )

_c0 carat cut color clarity depth table price x y z rank 27415 2.05 Ideal G SI2 61.6 56.0 18017 8.11 8.16 5.01 1 27630 2.22 Ideal I VS2 61.3 56.0 18531 8.45 8.36 5.15 2 27130 2.04 Ideal J IF 61.5 58.0 17327 8.11 8.14 5.0 3 25999 4.01 Premium I I1 61.0 61.0 15223 10.14 10.1 6.17 4 25998 1.01 Very Good D IF 63.4 59.0 15219 6.39 6.26 4.01 5 26444 2.0 Very Good H SI1 63.2 58.0 15984 7.95 7.93 5.02 6 26534 2.02 Very Good I SI1 59.8 59.0 16192 8.21 8.3 4.94 7 23645 3.65 Fair H I1 67.1 53.0 11668 9.53 9.48 6.38 8 27679 2.02 Ideal G VS2 62.0 57.0 18700 8.1 8.05 5.01 9 24328 1.5 Premium E VS2 59.4 62.0 12587 7.48 7.4 4.42 10 26431 2.0 Good E SI2 60.1 54.0 15962 8.01 8.15 4.86 11 24131 1.59 Very Good H VVS2 63.0 58.0 12297 7.43 7.48 4.7 12 24297 1.51 Ideal F SI1 62.8 57.0 12545 7.28 7.33 4.59 13 21759 3.11 Fair J I1 65.9 57.0 9823 9.15 9.02 5.98 14 22429 3.05 Premium E I1 60.9 58.0 10453 9.26 9.25 5.66 15 27638 1.72 Very Good E VS2 63.4 56.0 18557 7.65 7.55 4.82 16 26100 2.0 Fair F SI2 70.2 57.0 15351 7.63 7.59 5.34 17 27649 2.03 Ideal F SI2 61.6 55.0 18578 8.19 8.14 5.03 18 22742 3.01 Fair H I1 56.1 62.0 10761 9.54 9.38 5.31 19 22832 3.0 Good I I1 57.0 64.0 10863 9.38 9.31 5.33 20 25850 2.0 Premium G SI1 59.0 62.0 14918 6.16 6.15 4.82 21 23540 3.0 Good E I1 64.2 65.0 11548 9.08 8.96 5.79 22 27517 3.01 Fair I SI2 65.8 56.0 18242 8.99 8.94 5.9 23 27518 3.01 Good I SI2 63.9 60.0 18242 9.06 9.01 5.77 23 27514 2.3 Premium I VS2 61.8 60.0 18239 8.47 8.39 5.21 24 26744 2.44 Very Good J VS2 60.1 59.0 16533 8.75 8.83 5.28 25 27684 2.0 Very Good E SI1 60.5 59.0 18709 8.09 8.14 4.94 26 27685 3.01 Premium J SI2 60.7 59.0 18710 9.35 9.22 5.64 27 25460 1.55 Ideal F SI1 61.9 55.0 14220 7.47 7.42 4.61 28 22541 3.02 Fair I I1 65.2 56.0 10577 9.11 9.02 5.91 29 26467 2.17 Good H SI2 58.9 62.0 16036 8.48 8.52 5.01 30 19340 3.01 Premium I I1 62.7 58.0 8040 9.1 8.97 5.67 31 24816 2.0 Very Good J VS1 61.0 51.6 13203 8.14 8.18 4.97 32 26932 2.28 Ideal E SI2 62.0 55.0 16969 8.49 8.45 5.25 33 21863 3.01 Premium F I1 62.2 56.0 9925 9.24 9.13 5.73 34 26933 3.0 Premium I SI2 60.7 59.0 16970 9.3 9.14 5.6 35 27515 3.01 Premium I SI2 60.2 59.0 18242 9.36 9.31 5.62 36 27516 3.01 Fair I SI2 65.8 56.0 18242 8.99 8.94 5.9 36 19347 3.0 Fair H I1 67.1 57.0 8044 8.93 8.84 5.97 37 16284 3.0 Very Good H I1 63.1 55.0 6512 9.23 9.1 5.77 38 25900 2.48 Fair I SI2 56.7 66.0 15030 8.88 8.64 4.99 39 27739 2.05 Ideal G SI1 61.9 57.0 18787 8.1 8.16 5.03 40 22400 2.77 Premium H I1 62.6 62.0 10424 8.93 8.83 5.56 41 26129 1.54 Ideal G VVS2 62.0 54.0 15415 7.36 7.43 4.59 42 27024 2.51 Ideal H SI2 62.0 57.0 17162 8.72 8.67 5.39 43 20463 2.74 Fair J I1 64.9 61.0 8807 8.76 8.66 5.65 44 24784 1.51 Good G VVS2 63.8 59.0 13155 7.24 7.28 4.63 45 27065 2.03 Ideal G SI2 61.1 57.0 17182 8.16 8.21 5.0 46 27016 1.5 Premium E VS1 59.5 61.0 17143 7.46 7.43 4.43 47 27302 2.01 Ideal F SI2 61.3 60.0 17798 8.05 8.1 4.95 48 23581 2.72 Ideal H I1 59.6 55.0 11594 9.17 9.13 5.45 49 17197 2.72 Fair J I1 68.2 56.0 6870 8.46 8.43 5.76 50 25525 2.0 Very Good H SI2 61.0 57.0 14340 8.02 8.18 4.94 51 19867 2.68 Premium G I1 58.6 60.0 8419 9.11 9.07 5.33 52 21567 2.68 Very Good I I1 63.5 56.0 9665 8.81 8.77 5.58 53 27672 1.42 Ideal F VVS1 60.8 56.0 18682 7.25 7.32 4.43 54 27616 2.0 Premium F SI1 62.6 59.0 18493 8.1 8.04 5.05 55 26592 1.53 Ideal G VS1 60.5 57.0 16311 7.42 7.52 4.51 56 26553 2.32 Premium F SI2 62.5 59.0 16237 8.51 8.44 5.3 57 26554 2.66 Good H SI2 63.8 57.0 16239 8.71 8.65 5.54 57 22414 2.63 Very Good J I1 62.3 61.0 10437 8.76 8.81 5.47 58 22579 2.63 Premium J I1 62.3 61.0 10628 8.81 8.76 5.47 58 27163 2.0 Good G SI1 63.6 61.0 17405 7.9 7.83 5.0 59 26908 2.01 Very Good I VS1 62.9 62.0 16914 7.98 8.02 5.03 60 25192 2.22 Very Good J SI1 58.7 60.0 13782 8.51 8.57 5.01 61 27080 1.71 Very Good G VS1 61.3 54.0 17206 7.69 7.74 4.73 62 27727 2.36 Premium H SI2 59.4 58.0 18745 8.69 8.75 5.18 63 27081 2.6 Premium J SI2 58.3 61.0 17209 9.05 8.94 5.24 64 25778 1.5 Premium E VS2 61.9 57.0 14745 7.38 7.31 4.55 65 269